In [83]:
from env import host, username, password, get_db_url
import os
import pandas as pd 
import numpy as np
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

from pandas_profiling import ProfileReport

Pandas backend loaded 1.3.4
Numpy backend loaded 1.20.3
Pyspark backend loaded 3.2.1
Python backend loaded


In [4]:
def acquire_zillow_data_again(use_cache=True):
    if os.path.exists('zillow_again.csv') and use_cache:
        print('Using cached CSV')
        return pd.read_csv('zillow_again.csv')
    print('Acquiring data from SQL database')
    df = pd.read_sql('''
                        SELECT bedroomcnt, 
                               bathroomcnt, 
                               calculatedfinishedsquarefeet, 
                               taxvaluedollarcnt, 
                               yearbuilt, 
                               fips,
                               lotsizesquarefeet
                        FROM properties_2017
                            JOIN propertylandusetype USING (propertylandusetypeid)
                            JOIN predictions_2017 USING(parcelid)
                        WHERE propertylandusedesc IN ('Single Family Residential', 
                                                        'Inferred Single Family Residential')
                            AND transactiondate LIKE '2017%%';
                    
                     '''
                    , get_db_url('zillow'))
    df.to_csv('zillow_again.csv', index=False)
    
    
    return df

In [15]:
df = acquire_zillow_data_again()

Using cached CSV


In [6]:
df.head()

bedroomcnt  bathroomcnt  calculatedfinishedsquarefeet  taxvaluedollarcnt  \
0         4.0          3.5                        3100.0          1023282.0   
1         2.0          1.0                        1465.0           464000.0   
2         3.0          2.0                        1243.0           564778.0   
3         4.0          3.0                        2376.0           145143.0   
4         4.0          3.0                        2962.0           773303.0   

   yearbuilt    fips  lotsizesquarefeet  
0     1998.0  6059.0             4506.0  
1     1967.0  6111.0            12647.0  
2     1962.0  6059.0             8432.0  
3     1970.0  6037.0            13038.0  
4     1950.0  6037.0            63000.0

In [59]:
def describe_data(df):
    print('The first three rows are: ')
    print('----------------------------------------------------------')
    print(df.head(3))
    print('----------------------------------------------------------')
    print("The data frame's shape is: ")
    print('-------------------------')
    print(f' Rows: {df.shape[0]} \n Columns: {df.shape[1]}')
    print('-------------------------')   
    print('The data types and column names are: ')
    print(sorted(df))
    print(df.info())
    print('----------------------------------------------------------')   
    print('The summary statistics are as follows: ')
    print('----------------------------------------------------------')
    print(df.describe())
    print('----------------------------------------------------------')      
    print(f'The number of NA\'s is:')
    print('-------------------------')
    print(df.isna().sum())
    print('-------------------------')
    print ('\nMissing values :  ', df.isnull().sum().values.sum())
    print('----------------------------------------------------------')  
    print('Unique Values for the Columns:')
    print('-------------------------')
    limit = 25
    for col in df.columns:
        if df[col].nunique() < limit:
            print(f'Column: {col} \n')
            #print(f'Unique Values: {sorted(df[col].unique())} \n')
            print(f'Absolute frequencies: \n {df[col].value_counts()} \n')
            print(f'Relative frequencies: \n {round(df[col].value_counts(normalize=True), 3)} \n')
        else: 
            print(f'Column: {col} \n')
            print(f'Range of Values: [{df[col].min()} - {df[col].max()}] \n')
        print('-----------------------')
    print('-------Done-zo-------------')

In [14]:
#describe_data(df)

# SERIOUS PLANNING. Ideas to Implement 

- Create three separate data frames for each count, LA, Ventura, and Orange. Look at the outliers in each of those and remove them individually, then merge the data frame. 
- Worrying about the cities or neighborhoods at this juncture (at my low-skill level) is impractical. There will be far too many unique values, as an example, there are 88 cities in Los Angeles (jsyk: 34 in Orange, 18 in Ventura)
- Because of the low impact on the dataframe, there is no reason whatsoever to consider imputing the values, UNLESS, this is done after the counties are subdivided and the median is calculated for each, seeing how this wouldn't be impacted by outliers. Nevertheless, Zillow has a lot of problems with their data. 
- When homes are listed as having 0 baths, this is highly suspect. 0 bedrooms is acceptable, as they could be classified as studios. 0 baths would perhaps make sense for homes from the Victorian Era, but this would also interferece with the model. Effectively, all homes before 1901 should be removed. Hopefully there won't be many, so as to be justifiable.
- Lot size square feet in california is just too interesting to dismiss. 

In [16]:
def prepare_zillow(df):
        #just in case there are blanks
    df = df.replace(r'^\s*$', np.NaN, regex=True)

    # hold off on this for a sec, I want to check something
    #df.dropna(axis=0, how='any', inplace=True)

     # modify two columns
    df['fips'] = df.fips.apply(lambda fips: '0' + str(int(fips)))
    df['fips'].replace({'06037': 'los_angeles', '06059': 'orange', '06111': 'ventura'}, inplace=True)
    
    #df['yearbuilt'] = df['yearbuilt'].astype(int)
    #df.yearbuilt = df.yearbuilt.astype(object) 

    #df['age'] = 2017-df['yearbuilt']
    
    #df = df.drop(columns='yearbuilt')

    df = df.rename(columns={
                        'calculatedfinishedsquarefeet': 'area',
                       'bathroomcnt': 'baths',
                        'bedroomcnt': 'beds',
                        'taxvaluedollarcnt':'tax_value',
                        'fips': 'county_name'}
              )

    #df = remove_outliers(df, 1.5, ['beds', 'baths', 'area', 'tax_value', 'age'])
    
    #df['age'] = df['age'].astype('int')
    
    return df

In [17]:
df = prepare_zillow(df)

In [18]:
describe_data(df)

The first three rows are: 
----------------------------------------------------------
   beds  baths    area  tax_value  yearbuilt county_name  lotsizesquarefeet
0   4.0    3.5  3100.0  1023282.0     1998.0      orange             4506.0
1   2.0    1.0  1465.0   464000.0     1967.0     ventura            12647.0
2   3.0    2.0  1243.0   564778.0     1962.0      orange             8432.0
----------------------------------------------------------
The data frame's shape is: 
-------------------------
 Rows: 52441 
 Columns: 7
-------------------------
The data types and column names are: 
['area', 'baths', 'beds', 'county_name', 'lotsizesquarefeet', 'tax_value', 'yearbuilt']
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 52441 entries, 0 to 52440
Data columns (total 7 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   beds               52441 non-null  float64
 1   baths              52441 non-null  float64
 2   area          

In [19]:

missing_count = df.isnull().sum() # the count of missing values
value_count = df.isnull().count() # the count of all values
missing_percentage = round(missing_count / value_count * 100, 2) # percentage of missing values
missing_df = pd.DataFrame({'count': missing_count, 'percentage': missing_percentage}) # create df
print(missing_df)

                   count  percentage
beds                   0        0.00
baths                  0        0.00
area                  82        0.16
tax_value              1        0.00
yearbuilt            116        0.22
county_name            0        0.00
lotsizesquarefeet    369        0.70


In [46]:
# There's a possibility that yearsbuilt's missing values are from the victorian era. I wan't to see all rows where the yearbuilt is less than 1902
# it accounts for less than 1 percent of the entire dataset and is worth just dropping all together. But I'll check for fun. 

df[df['yearbuilt'] < 1902].value_counts().head()

beds  baths  area    tax_value  yearbuilt  county_name  lotsizesquarefeet
1.0   1.0    700.0   11683.0    1901.0     los_angeles  2477.0               1
4.0   2.0    1432.0  39834.0    1901.0     orange       6750.0               1
3.0   2.0    2568.0  243827.0   1898.0     los_angeles  21458.0              1
             1771.0  143776.0   1878.0     los_angeles  5126.0               1
             1732.0  280700.0   1890.0     los_angeles  8063.0               1
dtype: int64

In [43]:
# that didn't give me what I wanted, but has clued me in on there being white space. Let's fix that. I want to do a shape comparison
print(f' Shape before correcting for white space: {df.shape}')
# kind of out of order since I analyzed this in the following line of code. 
print(f' Shape before correcting for white space: {df2.shape}')
# something is definitely amiss. 

 Shape before correcting for white space: (52288, 7)
 Shape before correcting for white space: (52288, 7)


In [49]:
# so how many blanks are there?
df2 = df.replace(r'^\s*$', np.NaN, regex=True)

In [53]:
print(sorted(df['beds'].unique()))
print(sorted(df['baths'].unique()))

[1.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 9.0, 10.0, 11.0, 12.0, 14.0]
[1.0, 1.5, 2.0, 2.5, 3.0, 3.5, 4.0, 4.5, 5.0, 5.5, 6.0, 6.5, 7.0, 7.5, 8.0, 8.5, 9.0, 10.0, 11.0, 13.0, 18.0]


In [20]:
# removing rows with 0 bed and 0 bath, as these can't even be imagined as studios. 
df[['beds', 'baths']][(df.beds == 0.0) & (df.baths == 0.0)].count()
# I wonder how dropping these will affect the total missing values

beds     105
baths    105
dtype: int64

In [22]:
df = df[(df['baths'] > 0) & (df['beds'] > 0)]

In [23]:
df[['beds', 'baths']][(df.beds == 0.0) & (df.baths == 0.0)].count()
# it worked, but what's the impact on the missing values? 

beds     0
baths    0
dtype: int64

In [24]:
missing_count = df.isnull().sum() # the count of missing values
value_count = df.isnull().count() # the count of all values
missing_percentage = round(missing_count / value_count * 100, 2) # percentage of missing values
missing_df = pd.DataFrame({'count': missing_count, 'percentage': missing_percentage}) # create df
print(missing_df)

                   count  percentage
beds                   0        0.00
baths                  0        0.00
area                   8        0.02
tax_value              1        0.00
yearbuilt             40        0.08
county_name            0        0.00
lotsizesquarefeet    357        0.68


In [27]:
# that took care of plenty of the yearbuilt issues. 
# this single row tax_value missing value is bugging me. 
df[df.tax_value.isnull()]

beds  baths    area  tax_value  yearbuilt county_name  \
42299   4.0    2.0  1197.0        NaN     1954.0      orange   

       lotsizesquarefeet  
42299             7210.0

In [32]:
# find other similar properties
df[(df.county_name == 'orange') & (df.baths == 2.0) & (df.beds == 4.0) & (df.yearbuilt == 1954) & (df.lotsizesquarefeet == 7210.0)].head()

beds  baths    area  tax_value  yearbuilt county_name  \
6198    4.0    2.0  1169.0   190786.0     1954.0      orange   
42299   4.0    2.0  1197.0        NaN     1954.0      orange   
44002   4.0    2.0  1546.0    68610.0     1954.0      orange   

       lotsizesquarefeet  
6198              7210.0  
42299             7210.0  
44002             7210.0

Well, would you look at that. With all other than area the same, the range between the two is ridiculous. And seeing that property with a considerably greater
area is one-hundred twenty-two thousand dollars cheaper just adds to my worries about this data's integrity. If I were to replace this based off the mean, I should at least put it
into a separate dataframe. I'll make a different dataframe for each county and merge them later.  

In [71]:
# Select all rows and columns where county_name == orange
orange = df[df['county_name'] == 'orange']

In [73]:
orange.shape

(14085, 7)

In [74]:
ventura = df[df['county_name'] == 'ventura']

In [75]:
ventura.shape

(4366, 7)

In [76]:
los_angeles = df[df['county_name'] == 'los_angeles']

In [77]:
los_angeles.shape

(33837, 7)

In [78]:
df.shape

(52288, 7)

In [79]:
14085 + 4366 + 33837

52288

In [ ]:
orange

In [81]:
import mitosheet
mitosheet.sheet(orange, view_df=True)

MitoWidget(analysis_data_json='{"analysisName": "UUID-0a6b2808-f8b9-4ec2-b307-e53b5ffd1481", "code": {"imports…

In [84]:
report = ProfileReport(orange)
report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]